In [1]:
# Run this cell to install DiffeRT and its dependencies, e.g., on Google Colab

try:
    import differt  # noqa: F401
except ImportError:
    import sys  # noqa: F401

    !{sys.executable} -m pip install differt[all]

# Multipath Coherence Map

This notebook aims at being a tutorial to reproduce the results presented in the paper
*Comparing Differentiable and Dynamic Ray
Tracing: Introducing the Multipath Coherence Map*.

If you find this tutorial useful and plan on using this tool for your publications,
please cite our work, see {ref}`citing`.

## Summary

In our work, we present the {abbr}`MCM (Multipath Coherence Map)`, a visual tool, along with two metrics,
to help determining the range of application of the Dynamic {abbr}`RT (Ray Tracing)` method. For further details, please refer to the paper.

The below implementation is far from being the most efficient, as it first aims at providing a nice visual output.

## Imports

As our code includes some non-trivial plots, we need to import quite a few Python modules.
All of them should be installed with `differt[all]`.

In [2]:
import hashlib
import random

import equinox as eqx
import jax.numpy as jnp
import numpy as np
import plotly.graph_objects as go
from jaxtyping import Array, Bool, Int
from plotly.colors import convert_to_RGB_255
from tqdm.notebook import tqdm, trange

from differt.geometry.paths import merge_cluster_ids
from differt.geometry.triangle_mesh import TriangleMesh
from differt.geometry.utils import min_distance_between_clusters, path_lengths
from differt.plotting import draw_image, draw_markers, reuse, set_defaults
from differt.scene.sionna import download_sionna_scenes, get_sionna_scene
from differt.scene.triangle_scene import TriangleScene

## Simple Urban Street Canyon Scenario

Street canyons are probably one of the most common types of scenarios studied in RT,
due to their simplicity to model, but also important presence in big cities.

Because we provide a compatibility layer with Sionna scenes, we will simply load the `'simple_street_canyon'` scene.

In [3]:
download_sionna_scenes()  # Let's download Sionna scenes (from the main branch)

In [4]:
set_defaults(
    "plotly"
)  # Our scene is simple, and Plotly is the best backend for online interactive plots :-)

file = get_sionna_scene("simple_street_canyon")
scene = TriangleScene.load_xml(file)
scene.plot()

In the cell below (hidden by default), we define quite a few utility functions to
get nice plots, but this code is not needed if you are only interested in the metrics,
and not the visual output.

In [5]:
def hashfun(*objects: bytes) -> bytes:
    m = hashlib.sha256()

    for obj in objects:
        m.update(obj)

    return m.digest()


def get_cluster_hashes(
    cluster_ids: Int[Array, " *batch"],
    mask: Bool[Array, "*batch num_path_candidates"],
) -> dict[int, bytes]:
    mask = mask.reshape(-1, mask.shape[-1])

    return {
        int(i): hashfun(mask[i, :].tobytes())
        for i in jnp.unique(cluster_ids, return_index=True)[1]
    }


def merge_cluster_ids_and_hashes(
    cluster_ids: Int[Array, " *batch"],
    new_cluster_ids: Int[Array, " *batch"],
    cluster_hashes: dict[int, bytes],
    new_cluster_hashes: dict[int, bytes],
) -> tuple[Int[Array, " *batch"], dict[int, bytes]]:
    ret_cluster_ids = merge_cluster_ids(cluster_ids, new_cluster_ids)

    ret_cluster_hashes = {}

    for index in jnp.unique(ret_cluster_ids, return_index=True)[1]:
        i = cluster_ids.ravel()[index]
        j = new_cluster_ids.ravel()[index]

        ret_cluster_hashes[int(index)] = hashfun(
            cluster_hashes[int(i)],
            new_cluster_hashes[int(j)],
        )

    return ret_cluster_ids, ret_cluster_hashes


def draw_mesh_2d(mesh: TriangleMesh, figure: go.Figure) -> None:
    assert mesh.object_bounds is not None

    for i, j in mesh.object_bounds:
        sub_mesh = mesh[i:j]

        (xs, ys, (_, z_max)) = sub_mesh.bounding_box.T

        layer = "below" if z_max < 1e-6 else None

        assert sub_mesh.face_colors is not None
        color = convert_to_RGB_255(sub_mesh.face_colors[0, :])

        figure.add_shape(
            type="rect",
            x0=xs[0],
            y0=ys[0],
            x1=xs[1],
            y1=ys[1],
            fillcolor=f"rgb{color!s}",
            layer=layer,
        )


def random_rgb(cluster_hash: bytes) -> str:
    rng = random.Random(cluster_hash)  # noqa: S311
    r = rng.randint(0, 255)
    g = rng.randint(0, 255)
    b = rng.randint(0, 255)
    return f"rgb({r},{g},{b})"


def create_discrete_colorscale(
    cluster_ids: Int[Array, " *batch"],
    cluster_hashes: dict[int, bytes],
    first_is_multipath_cluster: bool,
) -> list[list[float | str]]:
    unique_ids = jnp.unique(cluster_ids).tolist()
    min_id = min(unique_ids)
    max_id = max(unique_ids)
    scale_factor = 1 + max_id - min_id

    def scale(id_: int) -> float:
        return (id_ - min_id) / scale_factor

    colorscale = [
        [scale(id_ + offset), random_rgb(cluster_hashes[id_])]
        for id_ in unique_ids
        for offset in (0, 1)
    ]

    if first_is_multipath_cluster:  # Let's hide the cluster with no multipath
        colorscale[0][1] = colorscale[1][1] = "rgba(0,0,0,0)"

    return colorscale

## Ray Tracing with a Grid of Receivers

Because we want to detect multipath clusters, we will need to perform RT simulations
for many receiving antenna location. The easiest way to do so is to use the
{meth}`Scene.with_receivers_grid<differt.scene.triangle_scene.TriangleScene.with_receivers_grid>`
method and rely on the global support of batched dimensions that this library offers to perform
many RT simulations at the same time.

:::{warning}
Beware that large batches or higher order reflection paths could rapidly cause out-of-memory issues!
:::

In the cell below, we also plot a dummy estimate of the received power, simply as a function of the inversed
squared of the path length.

In [6]:
# Let's put one transmitter and many receivers in our scene
scene = eqx.tree_at(lambda s: s.transmitters, scene, jnp.array([-33.0, 0.0, 32.0]))
# Our scene can be simplified to quadrilaterals,
# so informing the code of that matter will make it run faster
scene = eqx.tree_at(lambda s: s.mesh.assume_quads, scene, replace=True)
batch = (
    100,
    100,
)  # Warning: a too large batch could easily cause OOM issues,
#    or you may want to reduce the 'chunk_size' value below.
z0 = 1.5  # The z coordinate of the receivers
scene_grid = scene.with_receivers_grid(*batch, height=1.5)

# Let's accumulate power (simplified here to 1/r^2 for our example)
power = jnp.zeros(batch)

# And also keep track of multipath clusters
cluster_ids = jnp.zeros(batch, dtype=jnp.int32)  # Multipath cluster indices
unique_cluster_ids = jnp.empty(
    (), dtype=jnp.int32
)  # Contains unique values of 'cluster_ids'
cluster_hashes = {0: b""}  # This is only use generate constant random color per cluster
has_multipath = jnp.zeros(
    batch, dtype=bool
)  # Will be true if a receiver has at least one valid ray path

# Only need for plotting purposes
x, y, z = jnp.unstack(scene_grid.receivers, axis=-1)


with reuse() as fig:
    scene.plot()

    for order in trange(0, 2, leave=False):
        for paths in tqdm(
            scene_grid.compute_paths(order=order, chunk_size=1_000), leave=False
        ):
            new_cluster_ids = paths.multipath_clusters()
            new_unique_cluster_ids = jnp.unique(new_cluster_ids)
            new_cluster_hashes = get_cluster_hashes(new_cluster_ids, paths.mask)
            has_multipath |= paths.mask.any(axis=-1)
            cluster_ids, cluster_hashes = merge_cluster_ids_and_hashes(
                cluster_ids, new_cluster_ids, cluster_hashes, new_cluster_hashes
            )
            power += (paths.mask / path_lengths(paths.vertices) ** 2).sum(axis=-1)

    draw_image(  # TODO: change colorbar label
        np.asarray(power),
        x=np.asarray(x[0, :]),
        y=np.asarray(y[:, 0]),
        z0=z0,
    )

# We set cluster ids with no multiple to -1 for easier identification

if not has_multipath.all():
    # Simple way to retrieve the cluster index that has no multipath
    cluster_id = jnp.max(cluster_ids, initial=0, where=~has_multipath)
    cluster_hashes[-1] = cluster_hashes.pop(int(cluster_id))

cluster_ids = jnp.where(has_multipath, cluster_ids, -1)

fig

  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

## Plotting a Multipath Coherence Map

From the previous simulation, and thanks to your utility functions,
plotting a MCM can be performed in a few lines.

In [7]:
# We renumber unique indices to be between 0 and num_unique_cluster_ids (excluded)
# Because `jax.numpy.unique` sorts entries, the first cluster id will always refer to
# the 'no multipath' cluster, if it exists.
unique_ids, renumbered_cluster_ids = jnp.unique(cluster_ids, return_inverse=True)
renumbered_cluster_ids = renumbered_cluster_ids.reshape(cluster_ids.shape)
renumbered_cluster_hashes = {
    i: cluster_hashes[int(id_)] for i, id_ in enumerate(unique_ids)
}
# We create a discrete colorscale
colorscale = create_discrete_colorscale(
    renumbered_cluster_ids,
    renumbered_cluster_hashes,
    first_is_multipath_cluster=bool(~has_multipath.all()),
)

with reuse() as fig:
    tx_x, tx_y, _ = scene_grid.transmitters.reshape(3, 1)
    draw_mesh_2d(scene.mesh, fig)
    fig.add_scatter(
        x=tx_x,
        y=tx_y,
        mode="markers+text",
        text=["tx"],
        marker={"color": "#EF553B", "size": 15},
        showlegend=False,
    )
    fig.add_heatmap(
        z=np.asarray(renumbered_cluster_ids),
        x=np.asarray(x[0, :]),
        y=np.asarray(y[:, 0]),
        colorscale=colorscale,
        showscale=False,
    )

    fig.update_layout(
        height=600,
        xaxis={"range": [x.min(), x.max()]},
        yaxis={"range": [y.min(), y.max()], "scaleanchor": "x", "scaleratio": 1},
    )

fig

## Metrics

In the two nexts sections, we show of to compute the two metrics presented in the paper.

### Area per Cluster

To estimate the area per cluster, we simply count the number of {abbr}`RX (receiver)` in each cluster, and multiply
it by the area per point (i.e., per RX) to obtain the area covered by each cluster.

In [8]:
length_x = x.max() - x.min()
length_y = y.max() - y.min()
surface = length_x * length_y
num_points = cluster_ids.size
surface_per_point = (
    surface / num_points
)  # ~ Roughly, because RXs are not placed at centers of tiles

unique_ids, points_per_cluster = jnp.unique(cluster_ids, return_counts=True)
points_per_cluster = points_per_cluster[
    unique_ids != -1
]  # We remove cluster with no multipath
points_per_cluster

Array([163, 189, 569,  67,  29, 122, 156,  46,  10,   6,   4, 192, 354,
       197, 228,  71,  17,  72,  12,  92, 170,   4,  36,  15,   1, 205],      dtype=int32)

In [9]:
import plotly.express as px

surface_per_cluster = points_per_cluster * surface_per_point

labels = {
    "x": "Surface",
    "y": "Normalized number of clusters occupying a given surface",
}
counts, bins = np.histogram(surface_per_cluster, bins=30)
bins = 0.5 * (bins[:-1] + bins[1:])

px.bar(
    x=bins,
    y=counts / counts.sum(),
    labels=labels,
)

### Average Minimal Inter-Cluster Distance

For each RX in each cluster, we compute the minimal distance that is must travel to
be in a different cluster. We then compute the average of the value, per cluster.

In [10]:
min_dist = min_distance_between_clusters(scene_grid.receivers, cluster_ids)

for cluster_id in jnp.unique(cluster_ids):
    same_cluster = cluster_ids == cluster_id
    mean_min_dist = jnp.mean(min_dist, where=same_cluster)
    std_min_dist = jnp.std(min_dist, where=same_cluster)

    print(  # noqa: T201
        f"Cluster id = {int(cluster_id):5d} has an average minimal distance "
        f"to next cluster of {float(mean_min_dist):5.2f} "
        f"(std: {float(std_min_dist):.2f})"
    )

Cluster id =    -1 has an average minimal distance to next cluster of 17.38 (std: 12.12)
Cluster id =    22 has an average minimal distance to next cluster of  4.29 (std: 2.60)
Cluster id =    36 has an average minimal distance to next cluster of  3.05 (std: 1.94)
Cluster id =    40 has an average minimal distance to next cluster of  3.37 (std: 2.00)
Cluster id =   236 has an average minimal distance to next cluster of  1.99 (std: 0.59)
Cluster id =  1035 has an average minimal distance to next cluster of  1.79 (std: 0.23)
Cluster id =  1139 has an average minimal distance to next cluster of  2.81 (std: 1.23)
Cluster id =  1800 has an average minimal distance to next cluster of  3.49 (std: 2.01)
Cluster id =  3698 has an average minimal distance to next cluster of  1.67 (std: 0.64)
Cluster id =  3859 has an average minimal distance to next cluster of  1.39 (std: 0.35)
Cluster id =  4063 has an average minimal distance to next cluster of  1.22 (std: 0.00)
Cluster id =  4164 has an avera

## Animating Over Multiple Transmitter Positions

Of course, one may be interested to study the evolution of the MCM with respect to the {abbr}`TX (transmitter)` position.

The code below shows how to produce a nice interactice plot handling multiple TX positions.

In [11]:
# TODO: animate this slider ? https://plotly.com/python/animations/

from plotly.subplots import make_subplots

fig = make_subplots(
    rows=2,
    cols=1,
    specs=[[{"type": "scene"}], [{"type": "heatmap"}]],
)

with reuse(figure=fig) as fig:
    scene.plot(tx_kwargs={"visible": False}, row=1, col=1)
    draw_mesh_2d(scene.mesh, fig)

    offset = len(fig.data)

    x_positions = jnp.linspace(x.min(), x.max())

    for x_pos in tqdm(x_positions, leave=False):
        scene_grid = eqx.tree_at(
            lambda s: s.transmitters,
            scene_grid,
            scene_grid.transmitters.at[0].set(x_pos),
        )
        cluster_ids = jnp.zeros(batch, dtype=jnp.int32)
        cluster_hashes = {0: b""}
        has_multipath = jnp.zeros(batch, dtype=bool)

        for order in trange(0, 2, leave=False):
            for paths in tqdm(
                scene_grid.compute_paths(order=order, chunk_size=1_000), leave=False
            ):
                new_cluster_ids = paths.multipath_clusters()
                new_cluster_hashes = get_cluster_hashes(new_cluster_ids, paths.mask)
                has_multipath |= paths.mask.any(axis=-1)
                cluster_ids, cluster_hashes = merge_cluster_ids_and_hashes(
                    cluster_ids, new_cluster_ids, cluster_hashes, new_cluster_hashes
                )

        if not has_multipath.all():
            cluster_id = jnp.max(cluster_ids, initial=0, where=~has_multipath)
            cluster_hashes[-1] = cluster_hashes.pop(int(cluster_id))

        cluster_ids = jnp.where(has_multipath, cluster_ids, -1)
        unique_ids, renumbered_cluster_ids = jnp.unique(
            cluster_ids, return_inverse=True
        )
        renumbered_cluster_ids = renumbered_cluster_ids.reshape(cluster_ids.shape)
        renumbered_cluster_hashes = {
            i: cluster_hashes[int(id_)] for i, id_ in enumerate(unique_ids)
        }
        colorscale = create_discrete_colorscale(
            renumbered_cluster_ids,
            renumbered_cluster_hashes,
            first_is_multipath_cluster=bool(~has_multipath.all()),
        )

        draw_markers(
            np.asarray(scene_grid.transmitters.reshape(-1, 3)),
            labels=["tx"],
            showlegend=False,
            visible=False,
            row=1,
            col=1,
        )

        tx_x, tx_y, _ = scene_grid.transmitters.reshape(3, 1)

        fig.add_scatter(
            x=tx_x,
            y=tx_y,
            mode="markers+text",
            text=["tx"],
            marker={"color": "#EF553B", "size": 15},
            showlegend=False,
            visible=False,
            row=2,
            col=1,
        )

        fig.add_heatmap(
            x=np.asarray(x[0, :]),
            y=np.asarray(y[:, 0]),
            z=np.asarray(renumbered_cluster_ids),
            colorscale=colorscale,
            hovertemplate="Cluster id: %{z}",
            showscale=False,
            visible=False,
            row=2,
            col=1,
        )

    steps = []

    assert len(fig.data) == offset + len(x_positions) * 3

    for i, _ in enumerate(x_positions):
        step = {
            "method": "update",
            "args": [
                {"visible": [False, True] + [False] * len(x_positions) * 3},
            ],
        }
        step["args"][0]["visible"][offset + 3 * i + 0] = (
            True  # Show TX position on scene
        )
        step["args"][0]["visible"][offset + 3 * i + 1] = (
            True  # Show TX position on coherence map
        )
        step["args"][0]["visible"][offset + 3 * i + 2] = True  # Show coherence map
        steps.append(step)

    sliders = [
        {
            "active": 0,
            "currentvalue": {"prefix": "TX index: "},
            "pad": {"t": 50},
            "steps": steps,
        }
    ]

    fig.data[offset + 0].visible = True
    fig.data[offset + 1].visible = True
    fig.data[offset + 2].visible = True

    fig.update_layout(
        height=1200,
        sliders=sliders,
        xaxis={"range": [x.min(), x.max()]},
        yaxis={"range": [y.min(), y.max()], "scaleanchor": "x", "scaleratio": 1},
    )

fig

  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]